# Limiting Turnover

The *standard mean-variance (Markowitz) portfolio selection model* determines an optimal investment portfolio that balances risk and expected return. In this notebook, we maximize the portfolio's expected return while constraining the admissible variance (risk) to a given maximum level. Please refer to the [annotated list of references](../literature.rst#portfolio-optimization) for more background information on portfolio optimization.

In this notebook, we rebalance an existing portfolio and add a *turnover constraint*. Turnover constraints restrict the transaction volume and can implicitly affect the number of transactions. They limit the distance between the initial portfolio and the rebalanced one and, as such, favor stable investment strategies, which align with the objectives of institutional investors.
Additionally, turnover constraints often mitigate what is sometimes referred to as the error-maximizing property of the classical mean-variance portfolio.
Turnover constraints can be used as substitutes or complements to transaction cost constraints. They are also somewhat related to the tracking concept in portfolio optimization.

In [1]:
# Install dependencies
%pip install numpy scipy gurobipy pandas matplotlib

Note: you may need to restart the kernel to use updated packages.


In [2]:
import gurobipy as gp
import pandas as pd
import numpy as np
import scipy.linalg as la
import random

In [3]:
# Hidden cell to avoid licensing messages
# when docs are generated.
with gp.Model():
    pass

Set parameter WLSAccessID


Set parameter WLSSecret


Set parameter LicenseID to value 2443533


WLS license 2443533 - registered to Gurobi GmbH


## Input Data

The following input data is used within the model:

- $S$: set of stocks
- $\mu$: vector of expected returns
- $\Sigma$: PSD variance-covariance matrix
    - $\sigma_{ij}$ covariance between returns of assets $i$ and $j$
    - $\sigma_{ii}$ variance of return of asset $i$

In [4]:
# Import some example data set
Sigma = pd.read_pickle("sigma.pkl")
mu = pd.read_pickle("mu.pkl")

## Formulation
The straightforward formulation of the turnover requirements results in a nonconvex optimization problem. However, the turnover constraint can be linearized and the optimization model can be equivalently reformulated as a *convex* quadratic optimization problem.

Incorporating a limit on turnover significantly expands the decision space; the number of decision variables is three times as large as the model without turnover constraints.

### Model Parameters

The following parameters are used within the model:

- $\bar\sigma^2$: maximal admissible variance for the portfolio return
- $\tau$: maximal turnover rate
- $x^0_i$: holdings of asset $i$ in the initial portfolio.
Usually, the initial portfolio is given by the previous trading period.
In this notebook, we choose a simple initial portfolio by heuristically approximating the minimum variance portfolio on at most 20 assets.

In [5]:
# Values for the model parameters:
V = 4.0  # Maximal admissible variance (sigma^2)
tau = 0.2  # Maximal turnover rate

# Initial portfolio
tmp = pd.Series(index=mu.index, data=la.solve(Sigma, np.ones(mu.shape), assume_a="pos"))
x0 = pd.Series(index=mu.index, data=np.zeros(mu.shape))
x0.loc[tmp.nlargest(20).index] = 1.0 / 20.0

### Decision Variables
We need three sets of decision variables:

1. The proportion of capital invested in each stock in the rebalanced portfolio. The corresponding vector of positions is denoted by $x$ with its component $x_i$ denoting the proportion of capital invested in stock $i$.

The other sets of variables distinguish between buys and sales:

2. The proportions of each stock *bought* and included in the rebalanced portfolio. The corresponding vector of positions is denoted by $x^+$ with its component $x^+_i$ denoting the proportion of capital representing the buy of stock $i$.

3. The proportions of each stock *sold* from the initial portfolio. The corresponding vector of sales is denoted by $x^-$ with its component $x^-_i$ denoting the proportion of capital representing the sale of stock $i$.

### Variable Bounds

Each position must be between 0 and 1; this prevents leverage and short-selling:

$$0\leq x_i\leq 1 \; , \;  i \in S$$

The buy and sell proportions must be non-negative:

$$ x_i^+, x_i^- \geq 0\; , \, i \in S$$

In [6]:
%%capture
# Create an empty optimization model
m = gp.Model()

# Add variables: x[i] denotes the proportion invested in stock i
x = m.addMVar(len(mu), lb=0, ub=1, name="x")
# Add variables: x_plus[i] denotes the proportion of stock i bought
x_plus = m.addMVar(len(mu), lb=0, ub=1, name="x_plus")
# Add variables: x_minus[i] denotes the proportion of stock i sold
x_minus = m.addMVar(len(mu), lb=0, ub=1, name="x_minus")

###  Constraints

The budget constraint ensures that all capital is invested:

$$\sum_{i \in S} x_i =1 $$

The final proportion of capital invested in a stock in the rebalanced portfolio is obtained by taking into account the buys and sells of this stock as well as the holdings in the initial portfolio:
\begin{equation*}
x_i = x^0_i + x^+_i - x^-_i \; , \; i \in S \tag{1}
\end{equation*}

The estimated risk must not exceed a prespecified maximal admissible level of variance $\bar\sigma^2$:

$$x^\top \Sigma x \leq \bar\sigma^2$$

In [7]:
%%capture
# Budget constraint: all investments sum up to 1
m.addConstr(x.sum() == 1, name="Budget_Constraint")

# Position rebalancing constraint, see formula (1) above
m.addConstr(x == x0.to_numpy() + x_plus - x_minus, name="Position_Balance")

# Upper bound on variance
m.addConstr(x @ Sigma.to_numpy() @ x <= V, name="Variance")

#### Turnover
The *turnover ratio* is defined as the sum of the absolute values of the differences between the positions in the initial and rebalanced portfolios.

Denoting by $x_i^0$ the position in asset $i$ in the initial portfolio and by $x_i$ the position in the rebalanced portfolio,
the turnover ratio is defined as

$$\sum_{i \in S} |x_i - x^0_i| $$

and represents the absolute difference between the holdings in the two portfolios.

Accordingly, the turnover constraint

$$ \sum_{i \in S} |x_i - x^0_i| \leq \tau  $$

is nonconvex.


#### Linearization of Turnover Constraint

We may assume that at least one of the two variables $x^+_i$ or $x^-_i$ is equal to zero for each asset $i$, thus:
\begin{equation*}
\sum_{i \in S} |x_i - x^0_i| = \sum_{i \in S} |x^+_i - x^-_i| = \sum_{i \in S} x^+_i + \sum_{i \in S} x^-_i
\end{equation*}
Therefore, the turnover constraint can be replaced with the following linear constraint:

\begin{equation*}
\sum_{i \in S} x^+_i + \sum_{i \in S} x^-_i \leq \tau\tag{2}
\end{equation*}

In [8]:
%%capture
# Linearized turnover constraint; see formula (2) above
m.addConstr(x_plus.sum() + x_minus.sum() <= tau, name="Turnover")

###  Objective Function
The objective is to maximize the expected return of the portfolio:
$$\max \mu^\top x $$

In [9]:
# Define objective: total expected return
m.setObjective(mu.to_numpy() @ x, gp.GRB.MAXIMIZE)

We now solve the optimization problem:

In [10]:
m.optimize()

Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (linux64 - "Ubuntu 24.04.1 LTS")


CPU model: AMD EPYC 7763 64-Core Processor, instruction set [SSE2|AVX|AVX2]


Thread count: 1 physical cores, 2 logical processors, using up to 2 threads


WLS license 2443533 - registered to Gurobi GmbH


Optimize a model with 464 rows, 1386 columns and 2772 nonzeros


...

   8   2.42005053e-01  2.42499892e-01  7.24e-12 5.00e-16  1.53e-07     0s


   9   2.42337440e-01  2.42375930e-01  1.99e-13 6.66e-16  1.19e-08     0s


  10   2.42343948e-01  2.42344877e-01  3.50e-11 5.00e-16  2.87e-10     0s


Barrier solved model in 10 iterations and 0.39 seconds (0.70 work units)


Optimal objective 2.42343948e-01


Display basic solution data; for clarity we've rounded all solution quantities to five digits.

In [11]:
print(f"Expected return before/after: {mu @ x0:.6f}/{m.ObjVal:.6f}")
print(f"Variance        before/after: {x0 @ Sigma @ x0:.6f}/{x.X @ Sigma @ x.X:.6f}")
print(f"Solution time:   {m.Runtime:.2f} seconds\n")

print(
    f"Number of positions: before {np.count_nonzero(x0[x0>1e-5])}, after {np.count_nonzero(x.X[x.X>1e-5])}"
)
print(f"Number of buys:      {np.count_nonzero(x_plus.X[x_plus.X>1e-5])}")
print(f"Number of sells:     {np.count_nonzero(x_minus.X[x_minus.X>1e-5])}")
print(f"Total turnover:      {np.abs(x.X - x0).sum():.6f}\n")

# Print all assets with either non-negligible position or transaction
df = pd.DataFrame(
    index=mu.index,
    data={
        "position": x.X,
        "transaction": x.X - x0,
        "turnover": np.abs(x.X - x0),
    },
).round(6)
df[(df["position"] > 1e-5) | (abs(df["transaction"]) > 1e-5)].sort_values(
    "turnover", ascending=False
)

Expected return before/after: 0.201269/0.242344
Variance        before/after: 3.844733/3.999991
Solution time:   0.39 seconds

Number of positions: before 20, after 23
Number of buys:      5
Number of sells:     2
Total turnover:      0.200000



position  transaction  turnover
NVDA   0.070261     0.070261  0.070261
PEAK   0.000000    -0.050000  0.050000
TFC    0.000000    -0.050000  0.050000
TSLA   0.011780     0.011780  0.011780
ENPH   0.006759     0.006759  0.006759
LLY    0.006514     0.006514  0.006514
DXCM   0.004687     0.004687  0.004687
EG     0.050000    -0.000000  0.000000
RF     0.050000    -0.000000  0.000000
WTW    0.050000    -0.000000  0.000000
NVR    0.050000     0.000000  0.000000
CL     0.050000    -0.000000  0.000000
DUK    0.050000    -0.000000  0.000000
CMA    0.050000    -0.000000  0.000000
ED     0.050000    -0.000000  0.000000
FRT    0.050000    -0.000000  0.000000
STT    0.050000    -0.000000  0.000000
AMCR   0.050000    -0.000000  0.000000
APD    0.050000    -0.000000  0.000000
ROP    0.050000    -0.000000  0.000000
PSA    0.050000    -0.000000  0.000000
V      0.050000     0.000000  0.000000
KO     0.050000    -0.000000  0.000000
GOOGL  0.050000     0.000000  0.000000
AEE    0.050000     0.000000  0.000000

From the solution statistics, we see that with 20% turnover we could significantly increase the expected return while only slightly increasing the risk.

## Takeaways
* A turnover constraint can be modeled using additional continuous decision variables for the amounts bought and sold.
* Rebalancing is modeled in the same way as when we start from an all-cash position by considering the difference between the initial holdings and the final position in the rebalanced portfolio instead of just the final position.